# American Option Pricing using Binomial Tree, with Automatic Differentiation for IV Estimation (extending technique to other Greeks)

This notebook tutorial is a walkthrough for pricing American options using the binomial model. It should be referred to alongside the mathematical proofs and tutorial side (Proofs), as it would be easier to understand. 

We use a classic binomial model to price American options, with the Cox-Ross-Rubinstein (CRR) method of parameter estimation (estimation of u and hence p using sigma). The binomial model is a simple, intuitive and effective way to price options, and it is a good starting point for understanding the mechanics of option pricing under risk-neutral, no-arbitrage assumptions. We do this through a vectorization approach, which is much faster than the standard approach of pricing each option separately and iteratively backwards, which will be explained in Proofs.

In addition to that, based on the paper "Using the Newton-Raphson Method with Automatic Differentiation to Numerically Solve the Implied Volatility of Stock Options via the Binomial Model" by Michael Klibanov et al. [https://arxiv.org/html/2207.09033v3], we use the Newton-Raphson method and the automatic differentiation technique to solve for the implied volatility of the option in a way that is computationally faster than Brent's root search method (secant and bisection method), with high accuracy (RMSE from Brent's root search method is almost 0).

Extension of Project: 
1. We add in one more argument in dividend yield in continuous time assumption.
2. We include the computation of the other Greeks using the same AD method, and therefore do surface plots for the Greeks.
3. All non-essential functions have been moved to a separate file (greeks_lib.py) for ease of use and organization.

### Workflow
1. Fetch Option Chain Data
2. Fetch Risk Free Rates
3. Calculate IV from Market Data
4. Evaluation
5. Extension of Project for the Other Greeks (Delta, Gamma, Theta, Rho)
6. Comparison with BSM model

### Basic Imports

In [1]:
# imports from prior created fucntions
import greeks_lib
from greeks_lib import bsm_get_greeks, fetch_option_chains, fetch_fred_rf, plot_all_greeks_surface, plot_greeks_surface

In [2]:
# basic imports
import numpy as np
import pandas as pd

from scipy.optimize import brentq
from sklearn.metrics import mean_squared_error

from scipy.stats import norm
from scipy.interpolate import griddata
import plotly.graph_objects as go
from plotly.subplots import make_subplots

import warnings
warnings.filterwarnings("ignore")

### 1. Fetch Option Data

In [3]:
option_chains_df = fetch_option_chains('AAPL', 0.05, 1, price_range = 0.4, type = 'c')
option_chains_df

Obtained options for AAPL at 2026-03-06
Obtained options for AAPL at 2026-03-13
Obtained options for AAPL at 2026-03-20
Obtained options for AAPL at 2026-03-27
Obtained options for AAPL at 2026-04-17
Obtained options for AAPL at 2026-05-15
Obtained options for AAPL at 2026-06-18
Obtained options for AAPL at 2026-07-17
Obtained options for AAPL at 2026-08-21
Obtained options for AAPL at 2026-09-18
Obtained options for AAPL at 2026-11-20
Obtained options for AAPL at 2026-12-18
Obtained options for AAPL at 2027-01-15


K      f         T  Volume          S0         q
0    220.0  58.88  0.060274    13.0  273.200012  0.000038
1    230.0  44.50  0.060274    16.0  273.200012  0.000038
2    235.0  39.84  0.060274    40.0  273.200012  0.000038
3    245.0  29.60  0.060274    16.0  273.200012  0.000038
4    255.0  21.60  0.060274    42.0  273.200012  0.000038
..     ...    ...       ...     ...         ...       ...
231  320.0  13.40  0.923288    10.0  273.200012  0.000038
232  330.0  10.80  0.923288    12.0  273.200012  0.000038
233  350.0   6.89  0.923288    26.0  273.200012  0.000038
234  360.0   5.39  0.923288    24.0  273.200012  0.000038
235  370.0   4.35  0.923288   180.0  273.200012  0.000038

[236 rows x 6 columns]

### 2. Fetch Risk Free Rates

We use Fred API to extract latest money market rates from Fred as Risk Free Rate. This is because money market rates are considered to be short rates in the US, with investment horizon typically of 3 months to 1 year. Therefore, as options typicallyare short term contracts, we use money market rates as risk free rates.

In [4]:
rf = fetch_fred_rf(r'FRED_api_key.txt')

Current Money Market Rates as of  2026-01-14 is:  0.0362


### 3. Calculate IV from Market Data

We first define the functions binomial_price and binomial_price_vega_ad. These will be our "engines" for a recursive method of calculation of the price (and vega, for the latter function) of the option; that means to calculate the option price today by backwards calculating the future outcomes of option values and discounting to today. Please do refer to Proofs for the full explanation on the mechanics.

#### Core functions

In [5]:
def binomial_price(S0, K, T, r, sigma, type='c'):
    """
    We calculate the price of option using binomial approach. 
    We assume that the stock price can move up or down by a factor of u or d in each time step, where
    d = 1/u, the reciprocal. This is to ensure that at N time steps, there will be N+1 possible outcomes.

    By default, number of time steps N = 5000, to try to assume continuous time when dt = T/N is small.
    For time complexity, setting N at a higher value will raise the calculation time significantly.

    For parameters u and d estimation, we use the Cox, Ross and Rubinstein (CRR) method, where:
    u = e^(sigma * sqrt(dt))
    d = 1/u
    p = (e^(r * dt) - d) / (u - d)

    We use a vectorized approach to a recursive method to calculate the option price.

    Args:
        S0 (float): Current stock price.
        K (float): Option strike price.
        T (float): Time to expiration in years.
        r (float): Expected return of the underlying asset. When there is a dividend payout q, r = rf - q, 
                    where rf is the risk free rate. This is because when there is a dividend payout, the 
                    price of the stock will drop by dividend amount at the time of payout, and hence, 
                    expected return will drop by q.
        sigma (float): Volatility of the stock.
        type (str): Option type, 'c' for call, 'p' for put.

    Returns:
    float: Option price.
    """
    N = round(5000 * T)
    dt = T / N # time step per layer should tend to 0 to assume continuous time

    a = np.exp(- r * dt) # discount by risk free rate
    
    u = np.exp(sigma * np.sqrt(dt)) # up state
    d = 1 / u # down state is reciprocal of up state
    p = (np.exp(r * dt) - d) / (u - d) # probability of up state

    # Array of stock prices at maturity, where t = T
    # s_ij = S_0 * u^(i) * d^(j) where i + j = N, hence:
    S_t = S0 * u ** np.arange(N,-1,-1) * d ** np.arange(0,N+1,1) # (N+1) x 1 vector

    # Hence, option prices at time T, the Nth step is as follows:
    if type == 'c':
        f = np.maximum(S_t - K, 0)
    elif type == 'p':
        f = np.maximum(K - S_t, 0)
    else:
        raise ValueError("Option type must be 'c' or 'p'.")
    
    # recursive calculation of option price at each time step, from N-1 to 0
    for i in range(N-1, -1, -1):
        S_t = S0 * u ** np.arange(i,-1,-1) * d ** np.arange(0,i+1,1) # N number of outcomes at N-1 step
        # value of options at previous step = discount * (p * all up steps * (1-p) * all down steps
        f_previous = a * (p * f[:-1] + (1-p) * f[1:]) # N number of outcomes at N-1 step
        f = f_previous

        # as american option has the ability to exercise at any time, it is always worth
        # at least the intrinsic value of the option, S_t - k for call, k - S_t for put
        if type == 'c':
            f = np.maximum(f, S_t - K)
        elif type == 'p':
            f = np.maximum(f, K - S_t)

    return f[0]

In [6]:
def binomial_price_vega_ad(S0, K, T, r, sigma, type='c'):
    """ 
    Function has been corrected for an incorrect calculation of exercise / continuity vega, where exercise
    Vega should be 0 as option no longer exists. Hence, IV cannot affect its price.
    
    This is an extension to the binomial_price function through simultaneous calculation of vega.
    At the same time of option price calculation, we also calculate the vega of the option through automatic
    differentiation method. Therefore, Vega at maturity in this case is assumed to be non-zero for
    computational purposes (chain rule needs non-zero values).

    Args:
        S0 (float): Current stock price.
        K (float): Option strike price.
        T (float): Time to expiration in years.
        r (float): Expected return of the underlying asset. When there is a dividend payout q, 
                    r = rf - q, where rf is the risk free rate.
        sigma (float): Volatility of the stock.
        type (str): Option type, 'c' for call, 'p' for put.

    Returns:
    float: Option price.
    float: Option Vega.
    """
    N = round(5000 * T)
    dt = T / N # time step per layer should tend to 0 to assume continuous time

    a = np.exp(- r * dt) # discount by risk free rate

    # binomial tree pricing parameters
    u = np.exp(sigma * np.sqrt(dt)) # up state
    d = 1 / u # down state is reciprocal of up state
    p = (np.exp(r * dt) - d) / (u - d) # probability of up state

    # vega tree parameters
    # partial derivative of probability of up state to volatility 
    # dp = sqrt(dt) * {(u - d) - [e^(r * dt) - d] * (u + d)} / (u - d) ** 2
    dp = np.sqrt(dt) * (d * (u - d) - (np.exp(r * dt) - d) * (u + d)) / (u - d) ** 2

    # Array of stock prices at maturity, where at time step = N
    # s_ij = S_0 * u^(i) * d^(j) where i + j = N, hence:
    S_t = S0 * u ** np.arange(N,-1,-1) * d ** np.arange(0,N+1,1) # (N+1) x 1 vector

    # array of option vega at maturity, where time step = N,
    # as S_t = S0 * e^(sigma * sqrt(dt) * (2 * i - N)), hence:
    v_t = np.sqrt(dt) * (2 * np.arange(N,-1,-1) - N) * S_t

    # Hence, option prices at time T, the Nth step is as follows, where vega is 0 when f = 0:
    if type == 'c':
        f = np.maximum(S_t - K, 0)
        v = np.where(S_t > K, v_t, 0) 
    elif type == 'p':
        f = np.maximum(K - S_t, 0)
        v = np.where(K > S_t, -v_t, 0)
    else:
        raise ValueError("Option type must be 'c' or 'p'.")
    
    # recursive calculation of option price and vega at each time step, from N-1 to 0
    for i in range(N-1, -1, -1):

        # one computation for efficiency
        up_steps = np.arange(i,-1,-1)
        down_steps = np.arange(0,i+1,1)

        # stock prices at current time step
        S_t = S0 * u ** up_steps * d ** down_steps # N number of outcomes at N-1 step
        
        # value of options at previous step = discount * (p * all up steps * (1-p) * all down steps
        f_continuation = a * (p * f[:-1] + (1-p) * f[1:]) # N number of outcomes at N-1 step
        # value of vega at previous step
        v_continuation = a * (dp * (f[:-1] - f[1:]) + p * v[:-1] + (1-p) * v[1:])
        # update option price and vega for the loop
        f = f_continuation
        v = v_continuation
        #  american option has the ability to exercise at any time, it is always worth at least the intrinsic value of the option:
        # S_t - k for call, k - S_t for put
        if type == 'c':
            f_intrinsic = np.maximum(S_t - K, 0)

        elif type == 'p':
            f_intrinsic = np.maximum(K - S_t, 0)

        # in the case where value of option is greater than intrinsic value, we exercise the option
        exercise = f_intrinsic > f
        
        # therefore, vega of option at the step N-1 would be exercise vega if option will be exercised,
        # else it will be the continuation vega
        f = np.where(exercise, f_intrinsic, f) # this function would therefore always be max(contiuation, exercise)
        v = np.where(exercise, 0, v) # we assume vega is 0 at exercise/maturity

    return f[0], v[0]


#### IV Derivation Functions

IV can be derived from market data through Brent's root search method, used as the most accurate way. However, it is computationally expensive and slow. Considering that we have many options to calculate IV for, plus time step dt is close to 0, that means that the pricing model will run many times, which will be inefficient but very accurate as Brent's is almost guaranteed to converge.

Hence, using Vega, the first partial derivative of the option price with respect to IV, a faster convergence method in Newton-Ralphson (Newton's) can be used, which may not work sometimes but is much faster than Brent's. A fallback to use Brent's is also included in the case where Newton's does not. For more details, look into Proofs.

In [7]:
def iv_brentq(S0, K, T, r, initial_guess_iv, f, type='c', verbose = False):
    """
    We solely use Brent's method to find the IV for American options. This is much easier to implement than Newton-Raphson
    but much slower as well.

    To disable print statements, set verbose to False.

    The workflow is as such:
    1. Check if the option is worth less than the intrinsic value. If so, return np.nan
    2. Use Brent's method to find the IV
    3. If there is no convergence, return np.nan

    Args:
        S0 (float): The current price of the underlying asset
        K (float): The strike price of the option
        T (float): The time to expiration of the option in years
        r (float): Expected return of the underlying asset. When there is a dividend payout q, r = rf - q, where rf is the risk free rate.
        initial_guess_iv (float): The initial guess for the IV
        f (float): The current price of the option
        type (str): The type of the option ('c' for call, 'p' for put)

    Returns:
        float: The IV of the option
    """
    if type == 'c':
        intrinsic_value = max(S0 - K, 0)
    elif type == 'p':
        intrinsic_value = max(K - S0, 0)
    if f < intrinsic_value:
        return np.nan # american options cannot be worth less than intrinsic value
    else:
        try:
            iv = brentq(lambda initial_guess_iv: binomial_price(S0, K, T, r, initial_guess_iv, type) - f, 0.001, 2)
            if verbose:
                print(f"Brent Converged for S0: {round(S0, 2)}, K: {round(K, 2)}, T: {round(T, 2)}, r: {round(r, 2)}, IV: {round(iv, 2)}, f: {round(f, 2)}")
            return iv
            
        except ValueError:
            if verbose:
                print("Brent's method failed, returning np.nan")
            return np.nan

In [8]:
def iv_vega_newton(S0, K, T, r, initial_guess_iv, f, type='c', max_iterations = 200, tolerance = 1e-6, verbose = False):
    """ 
    Newton-Ralphson method can be used to estimate IV for american options due to existence of vega function from
    the backwards induction and automatic differentiation method in the binomial tree. Returns IV and Vega.

    To disable print statements, set verbose to False.

    The workflow is as such:
    1. Check if the option is valid (f > intrinsic value)
    2. Attempt Newton-Raphson method first.
    3. If Newton-Raphson method fails, use Brent's method as a fallback.
    4. If there is no convergence or Brent's method fails, return np.nan

    Args:
        S0 (float): Current price of the underlying asset
        K (float): Strike price of the option
        T (float): Time to expiration in years
        r (float): Expected return of the underlying asset. When there is a dividend payout q, r = rf - q, where rf is the risk free rate.
        initial_guess_iv (float): Initial guess for the IV
        f (float): Option price
        type (str, optional): Type of option ('c' for call, 'p' for put). Defaults to 'c'.
        max_iterations (int, optional): Maximum number of iterations for the Newton-Raphson method. Defaults to 200.
        tolerance (float, optional): Tolerance for convergence. Defaults to 1e-6.

    Returns:
        tuple: (IV, Vega)
    """

    iv_trial = initial_guess_iv
    # first filter out options with intrinsic value > option value, as american options cannot be worth less than intrinsic value
    if verbose:
        print(f"Initial IV: {round(iv_trial, 2)}, f: {round(f, 2)}, S0: {round(S0, 2)}, K: {round(K, 2)}, T: {round(T, 2)}, r: {round(r, 2)}, type: {type}")
    if type == 'c':
        intrinsic_value = max(S0 - K, 0)
    elif type == 'p':
        intrinsic_value = max(K - S0, 0)
    if f < intrinsic_value:
        if verbose:
            print("Intrinsic value is greater than option price, returning np.nan")
        return np.nan, np.nan
        
    for i in range(max_iterations):
        price_trial, vega_trial = binomial_price_vega_ad(S0, K, T, r, iv_trial, type)
        iv_previous = iv_trial # store value first for convergence check

        try: # fast newton raphson method
            if abs(vega_trial) < 1e-5: # vega can potentially be very small. hence, to prevent division by zero, go into fallback method
                if verbose:
                    print("Vega is too small, using Brent's method instead")
                raise ZeroDivisionError()
            # newton raphson method
            iv_trial = iv_trial - (price_trial - f) / vega_trial # Next IV Estimate = Old IV Estimate - f(iv)/f'(iv)
            # convergence check
            if abs(iv_trial - iv_previous) < tolerance: # convergence check if iv_trial is close enough to the previous iv_trial
                if verbose:
                    print(f"Newton-Raphson Converged for S0: {round(S0, 2)}, K: {round(K, 2)}, T: {round(T, 2)}, r: {round(r*100, 2)}, IV: {round(iv_trial, 2)}, f: {round(f, 2)}, vega: {round(vega_trial, 2)}")
                return iv_trial, vega_trial 
        # fallback brent method
        except Exception as e:
            if verbose:
                print("Error, Brent's method used instead")
            break
    try:
        iv_trial = brentq(lambda initial_guess_iv: binomial_price_vega_ad(S0, K, T, r, initial_guess_iv, type)[0] - f, 0.001, 3) #only take price
        vega_trial = binomial_price_vega_ad(S0, K, T, r, iv_trial, type)[1] # use the converged iv_trial to get vega from the binomial function
        if verbose:
            print(f"Brent Converged for S0: {round(S0, 2)}, K: {round(K, 2)}, T: {round(T, 2)}, r: {round(r, 2)}, IV: {round(iv_trial, 2)}, f: {round(f, 2)}, vega: {round(vega_trial, 2)}")
        return iv_trial, vega_trial
    except Exception as e: # if brent method fails, return np.nan
        if verbose:
            print("Brent's method failed, returning np.nan")
        return np.nan, np.nan

#### Newton's Method

In [9]:
def get_iv_vega_newton(df, rf, type='c'):
    """
    Estimates the implied volatility (IV) for a given option chain using the Newton Ralphson method. This is for use
    with the binomial_pricing_vega_ad and the iv_newton function. Variables are first vectorized for faster
    performance.

    These functions are much faster than only using Brent's method in the iv_brentq function, completing this
    task in less than half the time.
    
    Args:
    df (pd.DataFrame): DataFrame containing option chain data with columns 'S0', 'K', 'T', 'f', and 'q'.
    rf (float): Risk-free interest rate.
    type (str): Option type ('c' for calls, 'p' for puts).
    
    Returns:
    pd.DataFrame: DataFrame containing option chain data with columns 'S0', 'K', 'T', 'f', 'r', 'iv', 'vega'.
    """
    # make a copy of the df to avoid modifying the original
    df = df.copy()
    
    # vectorize variables
    S0 = df['S0'].values
    K = df['K'].values
    T = df['T'].values
    f = df['f'].values
    q = df['q'].values
    r = rf - q # expected return would be rf - q, as q is therefore the cost of carry of the option.

    df['r'] = r

    # vectorize the iv_newton function
    vec_iv_function = np.vectorize(iv_vega_newton, otypes=[float, float])

    df['iv'], df['vega'] = vec_iv_function(S0, K, T, r, 1, f, type)

    # clean up options where IV is not found
    df.dropna(inplace=True)
    df.reset_index(drop=True, inplace=True)

    df = df[['K', 'f', 'T', 'S0', 'r', 'iv', 'vega']]
    
    return df

In [10]:
df_iv_vega_newton = get_iv_vega_newton(option_chains_df, rf)
df_iv_vega_newton

K      f         T          S0         r        iv       vega
0    220.0  58.88  0.060274  273.200012  0.036162  0.941371  15.444655
1    230.0  44.50  0.060274  273.200012  0.036162  0.466506   7.735111
2    235.0  39.84  0.060274  273.200012  0.036162  0.457006   9.259061
3    245.0  29.60  0.060274  273.200012  0.036162  0.335381  10.926393
4    255.0  21.60  0.060274  273.200012  0.036162  0.363629  18.288287
..     ...    ...       ...         ...       ...       ...        ...
227  320.0  13.40  0.923288  273.200012  0.036162  0.250441  96.421421
228  330.0  10.80  0.923288  273.200012  0.036162  0.247527  91.784952
229  350.0   6.89  0.923288  273.200012  0.036162  0.243277  74.863237
230  360.0   5.39  0.923288  273.200012  0.036162  0.240689  67.834363
231  370.0   4.35  0.923288  273.200012  0.036162  0.241193  60.326193

[232 rows x 7 columns]

#### Brent's Method

In [11]:
def get_iv(df, rf, type='c'):
    df = df.copy()
    S0 = df['S0'].values
    K = df['K'].values
    T = df['T'].values
    f = df['f'].values
    q = df['q'].values
    r = rf - q # expected return would be rf - q, as q is therefore the cost of carry of the option.

    df['r'] = r

    vec_iv_function = np.vectorize(iv_brentq)

    df['iv'] = vec_iv_function(S0, K, T, rf, 1, f, type)

    df.dropna(inplace=True)
    df.reset_index(drop=True, inplace=True)
    return df

In [12]:
df_iv = get_iv(option_chains_df, rf)
df_iv

K      f         T  Volume          S0         q         r        iv
0    220.0  58.88  0.060274    13.0  273.200012  0.000038  0.036162  0.941345
1    230.0  44.50  0.060274    16.0  273.200012  0.000038  0.036162  0.466443
2    235.0  39.84  0.060274    40.0  273.200012  0.000038  0.036162  0.456953
3    245.0  29.60  0.060274    16.0  273.200012  0.000038  0.036162  0.335335
4    255.0  21.60  0.060274    42.0  273.200012  0.000038  0.036162  0.363604
..     ...    ...       ...     ...         ...       ...       ...       ...
227  320.0  13.40  0.923288    10.0  273.200012  0.000038  0.036162  0.250411
228  330.0  10.80  0.923288    12.0  273.200012  0.000038  0.036162  0.247501
229  350.0   6.89  0.923288    26.0  273.200012  0.000038  0.036162  0.243253
230  360.0   5.39  0.923288    24.0  273.200012  0.000038  0.036162  0.240667
231  370.0   4.35  0.923288   180.0  273.200012  0.000038  0.036162  0.241172

[232 rows x 8 columns]

### 4. Evaluation

In [13]:
plot_greeks_surface(df_iv,'iv')

In [14]:
plot_greeks_surface(df_iv_vega_newton,'iv')

Looks to be extremely similar. We will use RMSE to check and be certain.

In [15]:
def rmse_iv(brent_df, newton_df):
    """
    Hence, assuming that Brent's method is the absolute correct method, we evaluate the accuracy of the newton method.
    """
    df1 = brent_df.copy()
    df2 = newton_df.copy()
    # merge to match the options data aside from IV
    rmse_df = df1.merge(df2, on=['S0', 'K', 'T', 'r'], how='inner')
    rmse_df.dropna(inplace=True) # remove na or missing values in case

    rmse = np.sqrt(mean_squared_error(rmse_df['iv_x'], rmse_df['iv_y']))
    
    print(f"RMSE: {rmse}")

In [16]:
rmse_iv(df_iv, df_iv_vega_newton)

RMSE: 4.767182355799842e-05


As RMSE is extremely close to 0, it can be concluded that Newton's method would be a better way of computing IV as it is faster and as accurate as Brent's.

### 6. Extension of Project for the Other Greeks (Delta, Gamma, Theta, Rho)

Hence, we define another function to calculate the greeks since we have all the variables we need: f, IV, S0, K, T, r. The recursive formulas for each of the greeks will be shown in proofs. 

In [17]:
def derive_greeks_from_tree(S0, K, T, r, iv, type='c', verbose = True):
    """
    Following a similar recursive method, the rest of the greeks, with exception of Gamma as it is a 2nd
    order derivative, which we will use the Finite Difference method to compute.

    We still assume that at maturity, the option greeks are non-zero, aside from gamma, which we assume as 0 due to
    a Dirac distribution and theoretical infinite value at option being ATM.

    Exercise Greeks will still be 0.

    Args:
        S0 (float): Current stock price.
        K (float): Option strike price.
        T (float): Time to expiration in years.
        r (float): Expected return of the underlying asset. When there is a dividend payout q, 
                    r = rf - q, where rf is the risk free rate.
        iv (float): Computed Implied Volatility of the stock.
        type (str): Option type, 'c' for call, 'p' for put.

    Returns:
    float: Option Delta.
    float: Option Gamma.
    """

    N = round(5000 * T)
    dt = T / N # time step per layer should tend to 0 to assume continuous time

    a = np.exp(- r * dt) # discount by risk free rate

    # binomial tree pricing parameters
    u = np.exp(iv * np.sqrt(dt)) # up state
    d = 1 / u # down state is reciprocal of up state
    p = (np.exp(r * dt) - d) / (u - d) # probability of up state

    #computation of derivative of p wrt r for computation of Rho
    dp_dr = (dt * np.exp(r * dt) )/ (u - d)

    # Array of stock prices at maturity, where at time step = N
    # s_ij = S_0 * u^(i) * d^(j) where i + j = N, hence:
    S_t = S0 * u ** np.arange(N,-1,-1) * d ** np.arange(0,N+1,1) # (N+1) x 1 vector

    # we do not need to compute most other greeks at terminal step as they will be 0, other than delta
    # which is 1 when S_t > K and -1 when S_t < K.
    rho = np.zeros(N+1) # as there is backwards computation, we need (N+!) array of 0

    # Hence, option prices at time T, the Nth step is as follows, where vega is 0 when f = 0:
    if type == 'c':
        f = np.maximum(S_t - K, 0)
        delta = np.where(S_t > K, 1, 0) # array for delta at Nth step
    elif type == 'p':
        f = np.maximum(K - S_t, 0)
        delta = np.where(K > S_t, -1, 0)
    else:
        raise ValueError("Option type must be 'c' or 'p'.")
    
    # recursive calculation of option price and delta at each time step, from N-1 to 0
    for i in range(N-1, -1, -1):

        up_steps = np.arange(i,-1,-1)
        down_steps = np.arange(0,i+1,1)

        S_t = S0 * u ** up_steps * d ** down_steps # N number of outcomes at N-1 step
        # value of options at previous step = discount * (p * all up steps * (1-p) * all down steps
        f_continuity = a * (p * f[:-1] + (1-p) * f[1:]) # N number of outcomes at N-1 step
        # value of delta at previous step
        delta_continuity = a* (p * delta[:-1] + (1-p) * delta[1:])
        #computation of rho at the previous step
        rho_continuity = a * (rho[:-1] * p + rho[1:] * (1-p)) - dt * a * (f[:-1] * p + f[1:] * (1 - p)) + a * dp_dr * (f[:-1] - f[1:])

        # to use finite difference method, we have to compute from step N Delta and S_t
        # to obtain step N-1 Gamma.
        # however, this gives N-1 outcomes of gamma from N number of Delta outcomes and S_t outcomes 
        # at the N-1th step. therefore, we have to set up a seperate exercise condition to compute gamma.
        gamma_continuity = (delta_continuity[:-1] - delta_continuity[1:]) / (S_t[:-1] - S_t[1:])

        # update option value, delta and gamma for the loop
        f = f_continuity
        delta = delta_continuity
        gamma = gamma_continuity
        rho = rho_continuity
 
        # early exercise consideration
        if type == 'c':
            f_intrinsic = S_t - K
            delta_exercise = 1
            rho_exercise = 0
        elif type == 'p':
            f_intrinsic = K - S_t
            delta_exercise = -1
            rho_exercise = 0

        exercise = f_intrinsic > f

        f = np.where(exercise, f_intrinsic, f)
        delta = np.where(exercise, delta_exercise, delta) # delta is 0 at exercise, similarly to vega
        rho = np.where(exercise, rho_exercise, rho)
        
        if len(gamma_continuity) > 0:
            gamma_exercise = exercise[:-1] | exercise[1:] # dimension reduction for N-1 outcomes at N-1 step
            gamma = np.where(gamma_exercise, 0, gamma) # therefore, gamma must also be 0 at exercise
            if len(gamma_continuity) == 1:
                gamma_0 = gamma[0]
    
    # estimation on the BSM PDE solution
    theta = r * f[0] - r * S0 * delta[0] - 1/2 * iv ** 2 * S0 ** 2 * gamma_0
            
    return delta[0], gamma_0, theta, rho[0]


In [18]:
def get_binomial_greeks(df, type='c'):
    df = df.copy()

    S0 = df['S0'].values
    K = df['K'].values
    T = df['T'].values
    iv = df['iv'].values
    r = df['r'].values

    vec_greeks_function = np.vectorize(derive_greeks_from_tree, otypes=[np.float64, np.float64, np.float64, np.float64])

    df['delta'], df['gamma'] , df['theta'], df['rho'] = vec_greeks_function(S0, K, T, r, iv, type)

    df.dropna(inplace=True)
    df.reset_index(drop=True, inplace=True)
    
    return df

In [19]:
df_binomial_greeks = get_binomial_greeks(df_iv_vega_newton, type='c')
df_binomial_greeks

K      f         T          S0         r        iv       vega  \
0    220.0  58.88  0.060274  273.200012  0.036162  0.941371  15.444655   
1    230.0  44.50  0.060274  273.200012  0.036162  0.466506   7.735111   
2    235.0  39.84  0.060274  273.200012  0.036162  0.457006   9.259061   
3    245.0  29.60  0.060274  273.200012  0.036162  0.335381  10.926393   
4    255.0  21.60  0.060274  273.200012  0.036162  0.363629  18.288287   
..     ...    ...       ...         ...       ...       ...        ...   
227  320.0  13.40  0.923288  273.200012  0.036162  0.250441  96.421421   
228  330.0  10.80  0.923288  273.200012  0.036162  0.247527  91.784952   
229  350.0   6.89  0.923288  273.200012  0.036162  0.243277  74.863237   
230  360.0   5.39  0.923288  273.200012  0.036162  0.240689  67.834363   
231  370.0   4.35  0.923288  273.200012  0.036162  0.241193  60.326193   

     log_moneyness     delta     gamma       theta        rho  
0         0.216577  0.791024  0.004522 -155.226275  10.545484  
1         0.172125  0.925957  0.004377  -43.089557  12.844511  
2         0.150619  0.909027  0.005243  -48.409108  12.782748  
3         0.108946  0.893052  0.008069  -41.622912  13.335552  
4         0.068941  0.782544  0.011986  -66.095117  11.871533  
..             ...       ...       ...         ...        ...  
227      -0.158117  0.251286  0.004770  -13.163712  74.729675  
228      -0.188888  0.216682  0.004453  -11.932911  64.777418  
229      -0.247729  0.142368  0.003487   -8.859003  47.063740  
230      -0.275900  0.118300  0.003104   -7.683638  39.269772  
231      -0.303299  0.096676  0.002680   -6.616164  33.097809  

[232 rows x 12 columns]

Therefore, we compare it to the BSM model (European Option) for sanity check and to observe the how the option to exercise leads to differences in IV and greeks. 

In [20]:
df_bsm_greeks = bsm_get_greeks(option_chains_df, rf=rf, option_type='c')
df_bsm_greeks

K      f         T          S0         r        iv     delta  \
0    220.0  58.88  0.060274  273.200012  0.036162  0.941836  0.855809   
1    230.0  44.50  0.060274  273.200012  0.036162  0.466608  0.942814   
2    235.0  39.84  0.060274  273.200012  0.036162  0.456767  0.921998   
3    245.0  29.60  0.060274  273.200012  0.036162  0.334997  0.918082   
4    255.0  21.60  0.060274  273.200012  0.036162  0.363648  0.799897   
..     ...    ...       ...         ...       ...       ...       ...   
227  320.0  13.40  0.923288  273.200012  0.036162  0.250448  0.345324   
228  330.0  10.80  0.923288  273.200012  0.036162  0.247512  0.296353   
229  350.0   6.89  0.923288  273.200012  0.036162  0.243257  0.211817   
230  360.0   5.39  0.923288  273.200012  0.036162  0.240694  0.175427   
231  370.0   4.35  0.923288  273.200012  0.036162  0.241197  0.147151   

        gamma       vega       theta        rho  
0    0.003594  15.229865 -125.315953  10.543547  
1    0.003665   7.694137  -37.487159  12.842993  
2    0.004760   9.782230  -44.733878  12.781089  
3    0.006736  10.151327  -36.209779  13.333817  
4    0.011482  18.783633  -63.784631  11.869859  
..        ...        ...         ...        ...  
227  0.005606  96.753462  -16.049538  74.733247  
228  0.005321  90.766433  -14.703454  64.781254  
229  0.004536  76.039400  -11.860471  47.067667  
230  0.004086  67.773807  -10.372282  39.273598  
231  0.003635  60.427320   -9.189389  33.101453  

[232 rows x 11 columns]

In [21]:
plot_all_greeks_surface(df_binomial_greeks)

In [22]:
plot_all_greeks_surface(df_bsm_greeks)

In [24]:
greeks = ['iv', 'delta', 'gamma', 'vega', 'theta', 'rho']

df_merged = df_binomial_greeks[['K', 'T', 'S0'] + greeks].merge(
    df_bsm_greeks[['K', 'T'] + greeks], 
    on=['K', 'T'], 
    suffixes=('_bin', '_bsm')
)

df_merged['log_moneyness'] = np.log(df_merged['S0'] / df_merged['K'])

# Pre-compute all differences
for greek in greeks:
    df_merged[f'{greek}_diff'] = df_merged[f'{greek}_bin'] - df_merged[f'{greek}_bsm']

# Grid for interpolation
x_axis = np.linspace(df_merged['log_moneyness'].min(), df_merged['log_moneyness'].max(), 50)
y_axis = np.linspace(df_merged['T'].min(), df_merged['T'].max(), 50)
X_interp, Y_interp = np.meshgrid(x_axis, y_axis)

# Create subplots
fig = make_subplots(
    rows=2, cols=3,
    specs=[[{'type': 'surface'}]*3 for _ in range(2)],
    subplot_titles=[f'{g.upper()} (Binomial - BSM)' for g in greeks],
    horizontal_spacing=0.02,
    vertical_spacing=0.08
)

# Plot each Greek difference
for idx, greek in enumerate(greeks):
    row, col = idx // 3 + 1, idx % 3 + 1
    
    x = df_merged['log_moneyness'].values
    y = df_merged['T'].values
    z = df_merged[f'{greek}_diff'].values
    
    # Filter outliers
    mask = np.abs(z) <= np.percentile(np.abs(z), 97.5)
    
    # Interpolate
    Z_interp = griddata((x[mask], y[mask]), z[mask], (X_interp, Y_interp), method='cubic')
    
    fig.add_trace(
        go.Surface(
            z=Z_interp, x=X_interp, y=Y_interp, 
            colorscale='RdBu_r',
            showscale=(idx == 0),
            connectgaps=True,
            cmid=0
        ),
        row=row, col=col
    )

# Update layout
fig.update_layout(
    title='American Binomial vs BSM Greeks Difference (Binomial - BSM)',
    width=1400, height=900,
    margin=dict(l=10, r=10, t=80, b=10)
)

for i in range(1, 7):
    scene = f'scene{i}' if i > 1 else 'scene'
    fig.update_layout(**{scene: dict(
        xaxis_title='Log M', yaxis_title='T', zaxis_title='Δ',
        xaxis=dict(tickfont=dict(size=8)),
        yaxis=dict(tickfont=dict(size=8)),
        zaxis=dict(tickfont=dict(size=8))
    )})

fig.show()

There is a slight difference in the greeks between the binomial and bsm models.